# MS-E2122 - Nonlinear Optimisation
## 1st exercise session
### Topias Terho 

This notebook contains some useful functions and examples on how to use them to complete the first set of exercises. Once completed, you will be able to use most of the packages and functions that we will need in the first few weeks of the course.

# Exercise 1.1 and 1.2

The following packages and functions may be useful

In [ ]:
using Plots  # For plotting


# a vector from -1 to 1 with 1000 entries
n = 1000
x = LinRange(-1,1,n)
f(x) = x.^2

# plot values f with x-axis specified in x
plot(x, f(x),
        legend = false,
          xlabel = "x", 
          ylabel = "f(x)"   )

# scatter plot
scatter!([0.5], [f(0.5)], color = :orange)

In [ ]:
using Plots  # For plotting

n = 1000
x = LinRange(-1,1,n)
y = LinRange(-1,1,n)
g(x,y) = x^2 + y^2

z = [g(x[i], y[j]) for j = 1:n, i = 1:n]

# contour plot
contour(x,y,z,

        legend  = false,
        clabels = true,
        clims = (-0.5,0.5),
        size = (900,900),
        aspect_ratio = :equal,
        xlim   = [-0.5, 0.5],
        ylim   = [-0.5, 0.5],
        xlabel = "x",
        ylabel = "y",
        title  = "Contour plot",)

# Exercise 1.3 and 1.4

In [ ]:
using ForwardDiff        # For computing derivatives with automatic differentiation

h(x) = x^2 + 3

D(h, x)  = ForwardDiff.derivative(h, x) # define a function to calculate the derivative of function g at point x

#example
println(D(h, 1))


b(x) = x[1]^2 + x[2] + 3

H(b,x) = ForwardDiff.hessian(b, x) # calculate the hessian matrix of function z at point x

#example
println(H(b,[1,1]))


# Exercise 1.5

In this notebook we will show how to solve the resource allocation problem from the first lecture with JuMP and Ipopt optimizer. It will be up to you to then try to implement the problem in the exercise.

In [ ]:
# Import necessary packages
using JuMP, Ipopt, Plots

## Input data
Formatting the data we will be using in the model

In [ ]:
# Resources and their availability
resources = ["R1" "R2"]
R = [24 6]
# Products and their profits
products = ["P1" "P2"]
P = [5 4]
# Resource requirements
A = [6 4; 1 2]

In [ ]:
# Converting arrays to dictionaries
# This is not strictly necessary, but makes building the model easier
# because the labels "R1", "R2" etc. can be used to refer to the elements instead of the array indices
r_dict = Dict(resources .=> R)
p_dict = Dict(products .=> P)
a_dict = Dict( (resources[i], products[j]) => A[i,j]
          for i in 1:length(resources), j in 1:length(products) )

## Building the model
We start with an empty JuMP (Julia for Mathematical Programming) model, then add the decision variables, objective function and constraints.

In [ ]:
# Start building an optimization model named "resource_allocation"
resource_allocation = Model(optimizer_with_attributes(Ipopt.Optimizer, "print_level" => 3));

In [ ]:
# Decision variables: the production amount for each product
# We definitely want this to be nonnegative, negative production wouldn't make sense
@variable(resource_allocation, x[products] >= 0)

In [ ]:
# Objective function: maximize total profit from selling the products
@objective(resource_allocation, Max, sum(p_dict[j]*x[j] for j in products))

In [ ]:
# Constraints as specified on the lecture slides.
# Note that constraints do not need a name, it can be omitted.
# However, naming the constraints makes it easier to debug your model
@constraint(resource_allocation, supply[i in resources], sum(a_dict[i,j]*x[j] for j in products) <= r_dict[i] )

## Checking the model and obtaining solutions
We check that the printed model matches what we have in the lecture material and solve it to optimality.

In [ ]:
# Print the model and solve it
println(resource_allocation)
optimize!(resource_allocation)

In [ ]:
# Extract results and print solution
obj_val = round(objective_value(resource_allocation), digits=1)
P1_val = round(value(x["P1"]), digits=1)
P2_val = round(value(x["P2"]), digits=1)
println("The maximum profit is $obj_val when $P1_val units of product 1 and $P2_val units of product 2 are produced.")